In [1]:
comp = dict()

In [30]:
duration = 'month'
times = 2
result = 'ModulationTemperature.mat'
result_file = '../../Results/' + result

In [31]:
import sys
sys.path.append('/home/arnout/Projects/Work/ModelicaRes/')
sys.path.append('/home/arnout/Projects/Work/python-highcharts')
sys.path.append('/home/arnout/Projects/Work/util')

from modelicares import SimRes, SimResList
from charts import plot, plotasync

import util as u
import numpy as np
import datetime

In [32]:
duration = u.toseconds(duration, minus=86400, times=times)
print duration

4713600


In [33]:
load_names = {
    'Total heat flow': ['hea.Q_flow'],
    'Heating heat flow': ['buildingTest.heatingSystem.QHeaSys', 'buildingTest1.heatingSystem.QHeaSys'],
    'Total energy use': ['ETot'],
    'District heating losses':['dHConnection.QLosses', 'dHConnection1.QLosses'],
    'District heating flow': [
        'dHConnection.districtHeatingPipe.Q1',
        'dHConnection.districtHeatingPipe.Q2',
        'dHConnection1.districtHeatingPipe.Q1',
        'dHConnection1.districtHeatingPipe.Q2'
    ]
}

In [34]:
data = SimRes(result_file)

In [35]:
# Equi-distant time vector
minutes = 15
points = duration / (60*minutes)
t = [60*minutes*i for i in range(24*(60/minutes), points)]
tjs = map(lambda u: u*1000, t)

dates = map(datetime.datetime.fromtimestamp, t)   

# Get the loads at times t
loads = dict()
for name, variables in load_names.iteritems():
    y = []
    for key in variables:
        v = data[key]
        if len(y) > 0:
            y = y + np.array(map(lambda u: u._value, v.values(t)))
        else:
            y = np.array(map(lambda u: u._value, v.values(t)))
    
    loads[name] = y
    
# Get the DHW load
y = loads['Total heat flow'] - loads['Heating heat flow'] - loads['District heating flow']
y[y<0] = 0 
loads['DHW heat flow'] = y

In [36]:
options = {
    'chart': {
        'zoomType': 'xy'
    },
    'legend': {
        'enabled': True
    }
}

series = []
for key, value in loads.iteritems():
    series.append(dict(name=key, data=np.array([tjs, value]).T))

plot(
    series, options, stock=True, show='inline', height=550, save=str(result)+'-powers.html',
    display=['Total heat flow', 'Heating heat flow', 'District heating flow', 'DHW heat flow'])

In [37]:
# Sort by power
ldc = dict()
for key, value in loads.iteritems():
    ldc[key] = sorted(value, lambda x,y: cmp(y, x))

# Create series array
series = []
for key, value in ldc.iteritems():
    series.append(dict(name=key, data=np.array([tjs, value]).T))

In [38]:
plot(series, options, show='inline', stock=True, height=550, save=str(result)+'-ldc.html',
    display=['Total heat flow', 'Heating heat flow', 'District heating flow', 'DHW heat flow'])

In [39]:
losses = loads['District heating losses']/loads['Total energy use']
series = dict(name='Losses', data=np.array([tjs, losses]).T)
plot(series, options, show='inline', stock=True, height=550, save=str(result)+'-losses.html')

In [40]:
str(result)

'ModulationTemperature.mat'

In [41]:
comp[result] = dict(loads=loads, ldc=ldc, losses=losses)

In [42]:
comp.keys()

['LowTemperature.mat', 'ModulationTemperature.mat']

In [52]:
series = []
for key, value in comp.iteritems():
    variables = ['District heating flow']
    for v in variables:
        series.append(dict(name=key + ' ' + v, data=np.array([tjs, value['loads'][v]]).T))
    
plot(series, options, show='inline', stock=True, height=550, save='comp-losses.html')

In [50]:
series = []
for key, value in comp.iteritems():
    variables = ['Total heat flow', 'Heating heat flow', 'District heating flow', 'DHW heat flow']
    for v in variables:
        series.append(dict(name=key + ' ' + v, data=np.array([tjs, value['ldc'][v]]).T))
    
plot(series, options, show='inline', stock=True, height=550, save='comp-ldc.html')

In [63]:
series = []
for key, value in comp.iteritems():
    series.append(dict(name='losses' + ' ' + key, data=np.array([tjs, value['losses']]).T))
    
plot(series, options, show='inline', stock=True, height=550, save='comp-rel-losses.html')

In [61]:
series = []

for key in ['buildingTest.occupant.TSet[1]', 'buildingTest.occupant.mDHW60C']:
    v = data[key]
    y = np.array(map(lambda u: u._value, v.values(t)))

    series.append(dict(name=key, data=np.array([tjs, y]).T))
    
plot(series, options, show='inline', stock=True, height=550, save='profiles.html')  